# Environment setup

You can setup the workspace of the application with:
```shell
pip install -r requirements.txt
```

In [1]:
# display module
import plotly.graph_objects as go

# common
import numpy as np
from scipy.interpolate import InterpolatedUnivariateSpline as spline
import os.path
import h5py

# homemade
from fomweb import sensitivity
from fomweb import analytic_noise
from fomweb import utils


# Sensitivity plot

## Data generation

In [2]:
# widget variables
noise_config = "redbook"
mission_duration = 4.5
tdi2 = True
display_mode = "x unified"

# data files
data_file = "reduced_4.5_yr.h5"
# data_file = "reduced_7.5_yr.h5"

# data downloads
data_link = 'https://wiki-lisa.in2p3.fr/fom-sites/dc_82_fmin_1e-4/site/reduced_4.5_yr.h5'
# data_link = 'https://wiki-lisa.in2p3.fr/fom-sites/dc_82_7.5y/site/reduced_7.5_yr.h5'

precalculated_data = {
    
}
other_data = {}

# tables
table_verification_gb = []
table_resolved_gb = []

In [5]:
# Verification binaries

## Row data download
if not os.path.exists("data/VGB.npy"):
    os.system('wget https://github.com/Salander619/AppStreamlit/raw/main/data/VGB.npy')

verification_gb_out = np.load("VGB.npy")

## Creation of table freq, sh and snr
table_verification_gb = sensitivity.compute_gb_sensitivity(
    catalog=verification_gb_out,
    noise=noise_config,
    duration=mission_duration
)

--2024-04-30 12:19:25--  https://github.com/Salander619/AppStreamlit/raw/main/data/VGB.npy
Résolution de github.com (github.com)… 140.82.121.4
Connexion à github.com (github.com)|140.82.121.4|:443… connecté.
requête HTTP transmise, en attente de la réponse… 302 Found
Emplacement : https://raw.githubusercontent.com/Salander619/AppStreamlit/main/data/VGB.npy [suivant]
--2024-04-30 12:19:25--  https://raw.githubusercontent.com/Salander619/AppStreamlit/main/data/VGB.npy
Résolution de raw.githubusercontent.com (raw.githubusercontent.com)… 185.199.109.133, 185.199.108.133, 185.199.111.133, ...
Connexion à raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443… connecté.
requête HTTP transmise, en attente de la réponse… 200 OK
Taille : 9592 (9,4K) [application/octet-stream]
Enregistre : ‘VGB.npy’

     0K .........                                             100% 23,6M=0s

2024-04-30 12:19:26 (23,6 MB/s) - ‘VGB.npy’ enregistré [9592/9592]



In [4]:
# Resolved binaries

## Row data download
if not os.path.exists(data_file):
    os.system('wget '+data_link)

## Computation of table freq, sh and snr
with h5py.File(data_file,'r') as f:
    resolved_dataset = f['cat']

    table_resolved_gb = sensitivity.compute_gb_sensitivity(
        catalog=resolved_dataset,
        noise=noise_config,
        duration=mission_duration,
    )

--2024-04-30 12:17:59--  https://wiki-lisa.in2p3.fr/fom-sites/dc_82_fmin_1e-4/site/reduced_4.5_yr.h5
Résolution de wiki-lisa.in2p3.fr (wiki-lisa.in2p3.fr)… 134.158.69.30
Connexion à wiki-lisa.in2p3.fr (wiki-lisa.in2p3.fr)|134.158.69.30|:443… connecté.
requête HTTP transmise, en attente de la réponse… 200 OK
Taille : 229738549 (219M) [text/plain]
Enregistre : ‘reduced_4.5_yr.h5’

     0K .......... .......... .......... .......... ..........  0% 1,14M 3m12s
    50K .......... .......... .......... .......... ..........  0% 5,86M 1m55s
   100K .......... .......... .......... .......... ..........  0% 2,03M 1m52s
   150K .......... .......... .......... .......... ..........  0% 6,95M 92s
   200K .......... .......... .......... .......... ..........  0% 5,80M 81s
   250K .......... .......... .......... .......... ..........  0% 16,3M 70s
   300K .......... .......... .......... .......... ..........  0% 50,3M 61s
   350K .......... .......... .......... .......... ..........  0% 53,2M 

In [ ]:
# 

In [ ]:
# 

In [ ]:
# 

## Plot creation and display

### Data initialisation

### Data preparation

In [6]:
## prepare the data

#noise
noise_instru = analytic_noise.InstrumentalNoise(name="redbook")
noise_confu = analytic_noise.ConfusionNoise()

freq        = np.logspace(-5, 0, 9990)
duration    = mission_duration  # years
# to control the +10000

# noise psd
sxx_noise_instru_only    = noise_instru.psd(freq,
                                            option="X")
sxx_confusion_noise_only = noise_confu.psd(freq,
                                            duration=duration,
                                            option="X")
sxx_noise = sxx_noise_instru_only + sxx_confusion_noise_only

# response
r_ = utils.fast_response(freq)
# NOISE SENSITIVITY
sh = spline(freq, sxx_noise_instru_only / r_)
sh_wd = utils.psd2sh(freq, sxx_noise, sky_averaging=False)

### Display of the curves

In [7]:
####### display the sensitivity curves
vf = []
vy = []

for vgb in table_verification_gb:
    vf.append(float(vgb["freq"]))
    vy.append(float(np.sqrt(vgb["freq"] * vgb["sh"])))

rb_vf = []
rb_vy = []

for vgb in table_resolved_gb:
    rb_vf.append(float(vgb["freq"]))
    rb_vy.append(float(np.sqrt(vgb["freq"] * vgb["sh"])))

## Figure creation

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=rb_vf,
    y=rb_vy,
    #visible='legendonly',
    mode='markers',
    marker={'color':'blue'},
    marker_symbol="circle",
    name="Resolved GBs",
    hovertemplate = "<b>%{hovertext}</b><br>f= %{x:.4f} Hz<br>h=%{y}",
))

fig.add_trace(
    go.Scatter(
        x=vf,
        y=vy,
        mode="markers",
        marker={"color": "red"},
        marker_symbol="hexagon",
        name="GBs",
        hovertemplate="<b>%{hovertext}</b><br>f= %{x:.4f} Hz<br>h=%{y}",
    )
)

fig.add_trace(
    go.Scatter(
        x=freq,
        y=np.sqrt(freq) * np.sqrt(sh(freq)),
        name="Instrumental Noise",
    )
)


fig.add_trace(
    go.Scatter(
        x=freq,
        y=np.sqrt(freq) * np.sqrt(20 / 3) * np.sqrt(sh_wd(freq)),
        name="LISA Noise (Instru+Confusion)",
    )
)


fig.update_xaxes(
    title_text="Frequency (Hz)",
    type="log",
    showgrid=True,
    showexponent="all",
    exponentformat="e",
)
fig.update_yaxes(
    title_text="Characteristic Strain (TODO)",
    type="log",
    showgrid=True,
)
fig.update_layout(xaxis={"range": [-5, 0]})
fig.update_layout(yaxis={"range": [-22, -15]})
fig.update_layout(template="ggplot2")

fig.update_layout(hovermode=display_mode)

fig.update_layout(
    legend={
        "orientation": "h",
        "yanchor": "bottom",
        "y": 1.02,
        "xanchor": "right",
        "x": 1,
    }
)

fig.update_layout(height=600, width=1000)
fig.show()

In [8]:
fig2 = go.Figure()
fig2.add_trace(go.Scatter(x=freq, y=sxx_noise_instru_only, name="instru"))

fig2.add_trace(
    go.Scatter(
        x=freq,
        y=sxx_confusion_noise_only,
        # visible='legendonly',
        name="confusion",
    )
)

fig2.update_xaxes(
    title_text="Frequency (Hz)",
    type="log",
    showgrid=True,
    showexponent="all",
    exponentformat="e",
)
fig2.update_yaxes(
    title_text="Characteristic Strain (TODO)",
    type="log",
    showgrid=True,
)
fig2.show()